# Imports

In [1]:
import json
from pathlib import Path
import pickle
from tqdm.auto import tqdm

from haystack.nodes.preprocessor import PreProcessor

In [2]:
proj_dir = Path.cwd().parent
print(proj_dir)

/home/ec2-user/RAGDemo


# Config

In [13]:
file_in = proj_dir / 'data/consolidated/simple_wiki.json'
file_out = proj_dir / 'data/processed/simple_wiki_processed.pkl'

# Preprocessing

Its important to choose good pre-processing options. 

Clean whitespace helps each stage of RAG. It adds noise to the embeddings, and wastes space when we prompt with it.

I chose to split by word as it would be tedious to tokenize here, and that doesnt scale well. The context length for most embedding models ends up being 512 tokens. This is ~400 words. 

I like to respect the sentence boundary, thats why I gave a ~50 word buffer.

In [4]:
pp = PreProcessor(clean_whitespace = True,
             clean_header_footer = False,
             clean_empty_lines = True,
             remove_substrings = None,
             split_by='word',
             split_length = 350,
             split_overlap = 50,
             split_respect_sentence_boundary = True,
             tokenizer_model_folder = None,
             language = "en",
             id_hash_keys = None,
             progress_bar = True,
             add_page_number = False,
             max_chars_check = 10_000)

[nltk_data] Downloading package punkt to /home/ec2-user/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


In [5]:
with open(file_in, 'r', encoding='utf-8') as f:
    list_of_articles = json.load(f)

In [6]:
documents = pp.process(list_of_articles)

Preprocessing:  83%|████████████████████████████████████████████████████████████████████████████████████████████████▌                   | 276427/332023 [02:12<00:20, 2652.57docs/s]Document 81972e5bc1997b1ed4fb86d17f061a41 is 21206 characters long after preprocessing, where the maximum length should be 10000. Something might be wrong with the splitting, check the document affected to prevent issues at query time. This document will be now hard-split at 10000 chars recursively.
Document 5e63e848e42966ddc747257fb7cf4092 is 11206 characters long after preprocessing, where the maximum length should be 10000. Something might be wrong with the splitting, check the document affected to prevent issues at query time. This document will be now hard-split at 10000 chars recursively.
Preprocessing: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 332023/332023 [02:29<00:00, 2219.16docs/s]


When we break a wikipedia article up, we lose some of the context. The local context is somewhat preserved by the `split_overlap`. Im trying to preserve the global context by adding a prefix that has the article's title.

You could enhance this with the summary as well. This is mostly to help the retrieval step of RAG. Note that the way Im doing it alters some of `haystack`'s features like the hash and the lengths, but those arent too necessary. 

A more advanced way for many business applications would be to summarize the document and add that as a prefix for sub-documents.

One last thing to note, is that it would be prudent (in some use-cases) to preserve the original document without the summary to give to the reader (retrieve with the summary but prompt without), but since this is a simple use-case I wont be doing that.

In [7]:
# Prefix each document's content
for document in tqdm(documents):
    if document.meta['_split_id'] != 0:
        document.content = f'Title: {document.meta["title"]}. ' + document.content

  0%|          | 0/268980 [00:00<?, ?it/s]

## Pre-processing Examples

In [8]:
documents[0]

<Document: {'content': "April (Apr.) is the fourth month of the year in the Julian and Gregorian calendars, and comes between March and May. It is one of the four months to have 30 days.\nApril always begins on the same day of the week as July, and additionally, January in leap years. April always ends on the same day of the week as December.\nThe Month.\nApril comes between March and May, making it the fourth month of the year. It also comes first in the year out of the four months that have 30 days, as June, September and November are later in the year.\nApril begins on the same day of the week as July every year and on the same day of the week as January in leap years. April ends on the same day of the week as December every year, as each other's last days are exactly 35 weeks (245 days) apart.\nIn common years, April starts on the same day of the week as October of the previous year, and in leap years, May of the previous year. In common years, April finishes on the same day of the

In [9]:
documents[1]

<Document: {'content': 'Title: April. In years immediately before common years, April finishes on the same day of the week as September of the following year, and in years immediately before leap years, March and June of the following year.\nApril is a spring month in the Northern Hemisphere and an autumn/fall month in the Southern Hemisphere. In each hemisphere, it is the seasonal equivalent of October in the other.\nIt is unclear as to where April got its name. A common theory is that it comes from the Latin word "aperire", meaning "to open", referring to flowers opening in spring. Another theory is that the name could come from Aphrodite, the Greek goddess of love. It was originally the second month in the old Roman Calendar, before the start of the new year was put to January 1.\nQuite a few festivals are held in this month. In many Southeast Asian cultures, new year is celebrated in this month (including Songkran). In Western Christianity, Easter can be celebrated on a Sunday betw

In [10]:
documents[10102]

<Document: {'content': 'Title: Chief Joseph. He knew he could not trust them anymore. He was tired of being considered a savage. He felt it was not fair for people who were born on the same land to be treated differently. He delivered a lot of speeches on this subject, which are still really good examples of eloquence. But he did not feel listened to, and when he died in his reservation in 1904, the doctor said he "died from sadness". He was buried in Colville Native American Burial Ground, in Washington State.', 'content_type': 'text', 'score': None, 'meta': {'id': '19310', 'revid': '16695', 'url': 'https://simple.wikipedia.org/wiki?curid=19310', 'title': 'Chief Joseph', '_split_id': 1, '_split_overlap': [{'doc_id': '4bdf9cecd46c3bfac6b225aed940e798', 'range': (0, 275)}]}, 'id_hash_keys': ['content'], 'embedding': None, 'id': '91bc8240c5d067ab24f35c11f8916fc6'}>

In [11]:
print(f'Number of Articles: {len(list_of_articles)}')
processed_articles = len([d for d in documents if d.meta['_split_id'] == 0])
print(f'Number of processed articles: {processed_articles}')
print(f'Number of processed documents: {len(documents)}')

Number of Articles: 332023
Number of processed articles: 237724
Number of processed documents: 268980


# Write to file

In [14]:
with open(file_out, 'wb') as handle:
    pickle.dump(documents, handle, protocol=pickle.HIGHEST_PROTOCOL)